# Experiment Notebook: Compounding Yields for Pool Validators (Model Extenstion 5 - WIP)

# Table of Contents
* [Experiment Summary](#Experiment-Summary)
* [Experiment Assumptions](#Experiment-Assumptions)
* [Experiment Setup](#Experiment-Setup)
* [Analysis 1: Extended Time-domain](#Analysis-1:-Extended-Time-domain)
* [Analysis 2: Sweep of Pool Size](#Analysis-2:-Sweep-of-Pool-Size)

# Experiment Summary 

Each discrete validator requires a 32 ETH deposit when initialized. A validator's effective balance – the value used to calculate validator rewards – is a maximum of 32 ETH. Any rewards a validator earns above and beyond the 32 ETH requirement do not contribute to their yields until they accrue an additional 32 ETH and create another validator instance. This prevents a solo validator from reinvesting their yields to receive compound interest.

On the other hand, stakers that utilise validator pools, on exchanges for example, can compound their returns by pooling the returns of multiple validators to initialize another validator with 32 ETH. The pooling of returns and initialization of a shared validator effectively results in compound interest for those utilising staking pools, potentially resulting in much higher yields, especially over longer periods of time, than that of solo / distributed validators.

The following experiment notebook investigates ...


# Experiment Assumptions

 
* AVG Pool Size captures the mean pool size accross all pool environments.
* Because pool sizes are captured as an average, new shared validator instances are initialised simultaneously across pools leading to sudden 'spikes' in new shared validator instances as pools accrue the target validator stake ammount at the same time. In reality, spikes such as these would not occur in this manner due to variations in pool sizes across different pool validator environments.
* The current implementation assumes all pool validators engage in pool yield compounding. The model could implement a parameter accounting for the fraction of validator pools engaging in pool compounding once more data is known.

# Experiment Setup

We begin with several experiment-notebook-level preparatory setup operations:

* Import relevant dependencies
* Import relevant experiment templates
* Create copies of experiments
* Configure and customize experiments 

Analysis-specific setup operations are handled in their respective notebook sections.

In [1]:
# Import the setup module:
# * sets up the Python path
# * runs shared notebook configuration methods, such as loading IPython modules
import setup

import copy
import logging
import numpy as np
import pandas as pd
import plotly.express as px

import experiments.notebooks.visualizations as visualizations
from experiments.run import run
from experiments.utils import display_code
from model.types import Stage
from model.system_parameters import validator_environments


time: 767 ms (started: 2021-10-16 15:09:51 +02:00)


In [2]:
# Enable/disable logging
logger = logging.getLogger()
logger.disabled = False

time: 17.4 ms (started: 2021-10-16 15:09:52 +02:00)


In [3]:
# Import experiment templates
import experiments.templates.extended_time_horizon as extended_time_horizon
import experiments.templates.pool_size_sweep_analysis as pool_size_sweep_analysis

time: 26.8 ms (started: 2021-10-16 15:09:52 +02:00)


# Analysis 1: Extended Time-domain

Simulate the model over a 10 year period and plot relevent metrics. 

In [4]:
experiment = extended_time_horizon.experiment
simulation_1 = copy.deepcopy(extended_time_horizon.experiment.simulations[0])

time: 19.9 ms (started: 2021-10-16 15:09:52 +02:00)


In [5]:
# Experiment configuration:

normal_adoption = simulation_1.model.params['validator_process'][0](_run=None, _timestep=None)


simulation_1.model.params.update({
    # New validators per epoch
    "stage": [Stage.ALL],
    #"validator_process": [lambda _run, _timestep: normal_adoption * 1],
    "avg_pool_size": [1, 10, 100, 200],
    "eth_price_process": [lambda _run, _timestep: 3000],
})


time: 22.3 ms (started: 2021-10-16 15:09:52 +02:00)


In [6]:
# Experiment execution
df_1, exceptions = run(simulation_1)

2021-10-16 15:09:52,650 - root - INFO - Running experiment
2021-10-16 15:09:52,654 - root - INFO - Starting simulation 0 / run 0 / subset 0
2021-10-16 15:09:52,851 - root - INFO - Starting simulation 0 / run 0 / subset 1
2021-10-16 15:09:53,037 - root - INFO - Starting simulation 0 / run 0 / subset 2
2021-10-16 15:09:53,221 - root - INFO - Starting simulation 0 / run 0 / subset 3
2021-10-16 15:09:53,397 - root - INFO - Experiment complete in 0.7457571029663086 seconds
2021-10-16 15:09:53,398 - root - INFO - Post-processing results
2021-10-16 15:09:55,092 - root - INFO - Post-processing complete in 1.6953701972961426 seconds
time: 2.46 s (started: 2021-10-16 15:09:52 +02:00)


## Visualizations

#### To Do:
* Create / use visualization plots in __init__.py
* Label all x-axis time as Date


In [7]:
px.line(
    df_1,
    x='timestamp',
    y=['pool_staas_validator_count', 'pool_hardware_validator_count', 'pool_cloud_validator_count', 'diy_hardware_validator_count', 'diy_cloud_validator_count'],
    animation_frame='avg_pool_size'
)

time: 924 ms (started: 2021-10-16 15:09:55 +02:00)


In [8]:
px.line(
    df_1,
    x='timestamp',
    y=['pool_staas_eth_staked', 'pool_hardware_eth_staked', 'pool_cloud_eth_staked', 'diy_hardware_eth_staked', 'staas_full_eth_staked'],
    animation_frame='avg_pool_size'
)

time: 790 ms (started: 2021-10-16 15:09:56 +02:00)


In [9]:
px.line(
    df_1,
    x='timestamp',
    y=['pool_staas_profit', 'pool_hardware_profit', 'pool_cloud_profit', 'diy_hardware_profit', 'diy_cloud_profit'],
    animation_frame='avg_pool_size'
)

time: 678 ms (started: 2021-10-16 15:09:56 +02:00)


In [11]:


px.line(
    df_1,
    x='timestamp',
    y=['pool_staas_staker_profit_yields_pct', 'pool_hardware_staker_profit_yields_pct', 'pool_cloud_staker_profit_yields_pct', 'diy_hardware_staker_profit_yields_pct'],
    animation_frame='avg_pool_size'
)


time: 511 ms (started: 2021-10-16 15:09:58 +02:00)


# Analysis 2: Sweep of Pool Size

Phase-space analysis showing metrics as a function of the average pool size for pool validators using pool compounding.

* In order to accurately account for the compounding of pool validator yeilds over time, we first simulate the model over the desired time-horizon.
* Then, we perform a phase-space analysis at the desired timestep (e.g. at year 10)


In [12]:
# Analysis-specific setup

time: 24.5 ms (started: 2021-10-16 15:09:58 +02:00)


In [13]:
# Fetch the pool-size sweep analysis experiment
experiment = pool_size_sweep_analysis.experiment
# Create a copy of the experiment simulation
simulation_2 = copy.deepcopy(experiment.simulations[0])

time: 28.6 ms (started: 2021-10-16 15:09:58 +02:00)


In [14]:
# Experiment configuration

normal_adoption = simulation_2.model.params['validator_process'][0](_run=None, _timestep=None)

simulation_2.model.params.update({
    "validator_process": [lambda _run, _timestep: normal_adoption], # New validators per epoch
    "stage": [Stage.ALL], 
    "eth_price_process": [lambda _run, _timestep: 3000],
    
})


# Select the year to simulate to:
YEAR = 5
TIMESTEP_ANALYSIS = YEAR * 12 # convert year to month

time: 26.4 ms (started: 2021-10-16 15:09:58 +02:00)


In [15]:
# Experiment execution
df_2, exceptions = run(simulation_2)

2021-10-16 15:09:58,818 - root - INFO - Running experiment
2021-10-16 15:09:58,821 - root - INFO - Starting simulation 0 / run 0 / subset 0
2021-10-16 15:09:58,864 - root - INFO - Starting simulation 0 / run 0 / subset 1
2021-10-16 15:09:58,938 - root - INFO - Starting simulation 0 / run 0 / subset 2
2021-10-16 15:09:58,986 - root - INFO - Starting simulation 0 / run 0 / subset 3
2021-10-16 15:09:59,037 - root - INFO - Starting simulation 0 / run 0 / subset 4
2021-10-16 15:09:59,091 - root - INFO - Starting simulation 0 / run 0 / subset 5
2021-10-16 15:09:59,137 - root - INFO - Starting simulation 0 / run 0 / subset 6
2021-10-16 15:09:59,191 - root - INFO - Starting simulation 0 / run 0 / subset 7
2021-10-16 15:09:59,247 - root - INFO - Starting simulation 0 / run 0 / subset 8
2021-10-16 15:09:59,309 - root - INFO - Starting simulation 0 / run 0 / subset 9
2021-10-16 15:09:59,361 - root - INFO - Starting simulation 0 / run 0 / subset 10
2021-10-16 15:09:59,415 - root - INFO - Starting 

2021-10-16 15:10:04,568 - root - INFO - Experiment complete in 5.748698949813843 seconds
2021-10-16 15:10:04,569 - root - INFO - Post-processing results
2021-10-16 15:10:17,248 - root - INFO - Post-processing complete in 12.68054723739624 seconds
time: 18.5 s (started: 2021-10-16 15:09:58 +02:00)


## Visualizations

#### To Do
* Set time analysis point in labels / headings

In [28]:
# To plot a specific point in time without having to re-run the simulation, 
# set TIMESTEP_ANALYSIS below and re-run the following cells.

YEAR = 10
TIMESTEP_ANALYSIS = YEAR * 12  # convert year to month

time: 21.2 ms (started: 2021-10-16 15:12:21 +02:00)


In [29]:
visualizations.plot_staker_profit_yields_over_pool_size(df_2, TIMESTEP_ANALYSIS)

time: 38.7 ms (started: 2021-10-16 15:12:22 +02:00)


In [25]:
visualizations.plot_profit_yields_over_pool_size(df_2, TIMESTEP_ANALYSIS)

time: 40.1 ms (started: 2021-10-16 15:12:06 +02:00)


In [19]:
visualizations.plot_profit_over_pool_size(df_2, TIMESTEP_ANALYSIS)

time: 49.7 ms (started: 2021-10-16 15:10:17 +02:00)


In [20]:
visualizations.plot_eth_staked_over_pool_size(df_2, TIMESTEP_ANALYSIS)

time: 79 ms (started: 2021-10-16 15:10:17 +02:00)
